## Deceptive Low-stock Messages
- Look for sites with changing stock levels; then manually inspect to find deceptive cases.
- Sites listed below contain false positives, which we eliminate in the manual analysis stage (i.e. they may not be deceptive).
- We use data from the "monitor" crawls, i.e. repeated visits of the same sites (see, Section 4.4 of the paper)

In [1]:
import sqlite3
import pandas as pd
import re
import json
import numpy as np
import os
from os.path import dirname, abspath, join
pd.options.display.max_colwidth = 500
pd.set_option("display.max_rows", 100000)
pd.options.display.html.use_mathjax = False


In [21]:
DB = "/media/gacar/6TB/dark-patterns/data/monitoring/stock_notifications_crawl/stock_notifications_crawl.sqlite"
con = sqlite3.connect(DB)
df = pd.read_sql("""
SELECT sv.site_url,
       sv.visit_id,
       se.inner_text,
       LOWER(se.inner_text) AS msg
  FROM SEGMENTS AS se
       LEFT JOIN
       site_visits AS sv ON se.visit_id = sv.visit_id
 WHERE msg LIKE '%high demand%' OR 
       msg LIKE '%selling fast%' OR 
       msg LIKE '%hurry%' OR 
       msg LIKE '%left in stock%' OR 
       msg LIKE '%only % in stock%' OR 
       msg LIKE '%only % left%' OR 
       msg LIKE '% in stock%' OR 
       msg LIKE '%low stock%' OR 
       msg LIKE '% left%' OR 
       msg LIKE '%limited stock%'    
 GROUP BY sv.site_url, sv.visit_id, se.inner_text
 ORDER BY sv.site_url DESC
""", con)

/media/gacar/6TB/dark-patterns/data/monitoring/stock_notifications_crawl/stock_notifications_crawl.sqlite


In [36]:
df.head(3)

site_url  \
0  https://zox.la/collections/imperial/products/go-with-the-flow-imperial-white-tips   
1  https://zox.la/collections/imperial/products/go-with-the-flow-imperial-white-tips   
2  https://zox.la/collections/imperial/products/go-with-the-flow-imperial-white-tips   

   visit_id      inner_text             msg  
0       135  354 items left  354 items left  
1       865  354 items left  354 items left  
2      1595  354 items left  354 items left

In [37]:
# ignore websites whose stock amounts remained the same between visits
grouped = df[df.inner_text.str.contains('[0-9]+')].groupby('site_url')
udf = grouped.filter(lambda x: len(set(x['inner_text'].tolist())) > 1)

In [38]:
# list sites while ignoring the duplicate (site, inner_text) pairs
udf.drop_duplicates(['site_url', 'inner_text']).sort_values(
    ['site_url', 'visit_id'], ascending=True)[['visit_id', 'site_url', 'inner_text']]

visit_id  \
32870       224   
32873       224   
32876       224   
32877       224   
32479       622   
32481       622   
32482       622   
32532      7192   
32534      7192   
32535      7192   
32863     34932   
31951       284   
31952       284   
31953       284   
31954      1014   
31955      1014   
31956      1014   
31958      1744   
31959      1744   
31960      1744   
31962      2474   
31963      2474   
31964      2474   
31967      3204   
31968      3204   
31969      3204   
31971      3934   
31972      3934   
31973      3934   
31975      4664   
31976      4664   
31977      4664   
31980      5394   
31981      5394   
31982      5394   
31985      6124   
31986      6124   
31987      6124   
31989      6854   
31990      6854   
31991      6854   
31992      7584   
31993      7584   
31995      8314   
31996      8314   
31998      9044   
31999      9044   
32001      9774   
32002      9774   
32003     10504   
32004     10504   
32005     11234   
32006     11234   
32007     11964   
32008     11964   
32009     12694   
32010     12694   
32011     13424   
32012     13424   
32014     14154   
32015     14154   
32016     14884   
32017     14884   
32018     15614   
32019     15614   
32020     16344   
32021     16344   
32023     17074   
32024     17074   
32026     17804   
32027     17804   
32029     18534   
32030     18534   
32031     19264   
32032     19264   
32033     19994   
32034     19994   
32035     20724   
32036     20724   
32038     21454   
32039     21454   
32040     22184   
32041     22184   
32043     22914   
32044     22914   
32047     23644   
32049     24374   
32050     24374   
32052     25104   
32053     25104   
32055     25834   
32056     25834   
32058     26564   
32061     27294   
32064     28024   
32067     28754   
32069     29484   
32072     30214   
32073     30214   
32074     30214   
32076     30944   
32077     30944   
32080     31674   
32084     32404   
32088     33134   
32089     33134   
32090     33134   
32092     33864   
32093     33864   
32095     34594   
32096     34594   
31853       485   
31854       485   
31709       594   
31712      2784   
31399       172   
31400       172   
31401       172   
31303       575   
31304       575   
31018       214   
31019       214   
30887       419   
30906     13559   
30924     20129   
30933     23779   
30939     25969   
30954     31079   
30957     32539   
30749       342   
30750       342   
30751       342   
30614       258   
30615       258   
30414       457   
30415       457   
30416       457   
30417       457   
30567     28197   
30568     28197   
30318       418   
30319       418   
30176       510   
30177       510   
30083       539   
30093      7839   
29795       397   
29796       397   
29797       397   
29798       397   
29799       397   
30031     34707   
29634       344   
29635       344   
29636       344   
29651      4724   
29520        60   
29521        60   
29527      2250   
29534      4440   
29548      9550   
29549      9550   
29425       119   
29426       119   
29281       619   
29282       619   
29283       619   
29284      1349   
29285      1349   
29287      2079   
29288      2079   
29290      2809   
29291      2809   
29293      3539   
29294      3539   
29300      4999   
29303      5729   
29305      6459   
29306      6459   
29309      7189   
29312      7919   
29314      8649   
29315      8649   
29317      9379   
29318      9379   
29324     10839   
29326     11569   
29342     15219   
29347     16679   
29350     17409   
29362     20329   
29363     20329   
29380     24709   
29405     30549   
29414     32739   
29422     34929   
28955       355   
28957       355   
28962      1085   
28967      1815   
28982      4005   
28997      6195   
28794        62   
28795       792   
28796       792   
28797       792   
28798       792   
28799       792   
28800       792   
28801       792  